# How to index, slice, modify, and delete data points

Very usually, we need to select, modify and even delete the data of certain shots. Here there is a short introduction on how to do that.

Let us start with importing the supporting packages and loading the data. In order to keep things ealier, here we will import all the packages, but not all of them will be us

## Load some example data

### Import supporting packages

In [1]:
# Set the system path for importing packages
# This is just because I put all example scripts in another folder
# You DO NOT need to do this 
# -------------- You do NOT need following part --------------
import sys
import os
sys.path.insert(0, os.path.abspath('..'))
# -------------- You do NOT need above part --------------

import copy
import glob
from datetime import datetime

# The package for data structure
import xarray as xr
import pandas as pd
import numpy as np

# The packages for working with uncertainties
from uncertainties import ufloat
from uncertainties import unumpy as unp
from uncertainties import umath

# The package for plotting
import matplotlib.pyplot as plt
plt.rcParams['font.size'] = 18 # Set the global font size

# -------------- The modules written by us --------------

# The packages for read data
from DataContainer.ReadData import read_hdf5_file, read_hdf5_global, read_hdf5_run_time, read_csv_file

# The packages for data analysis
from Analyser.ImagingAnalyser import ImageAnalyser
from Analyser.FitAnalyser import FitAnalyser
from Analyser.FitAnalyser import ThomasFermi2dModel, DensityProfileBEC2dModel, Polylog22dModel
from Analyser.FFTAnalyser import fft, ifft, fft_nutou
from ToolFunction.ToolFunction import *

# Add errorbar plot to xarray package
from ToolFunction.HomeMadeXarrayFunction import errorbar, dataarray_plot_errorbar
xr.plot.dataarray_plot.errorbar = errorbar
xr.plot.accessor.DataArrayPlotAccessor.errorbar = dataarray_plot_errorbar

### Start a client for parallel computing

In [2]:
from dask.distributed import Client
client = Client(n_workers=6, threads_per_worker=10, processes=True, memory_limit='10GB')
client

<Client: 'tcp://127.0.0.1:62125' processes=6 threads=60, memory=55.88 GiB>

### Set the path for different cameras

In [3]:
groupList = [
    "images/MOT_3D_Camera/in_situ_absorption",
    "images/ODT_1_Axis_Camera/in_situ_absorption",
    "images/ODT_2_Axis_Camera/in_situ_absorption",
]

# give a short name to each path (or let's say each camera)
dskey = {
    "images/MOT_3D_Camera/in_situ_absorption": "camera_0",
    "images/ODT_1_Axis_Camera/in_situ_absorption": "camera_1",
    "images/ODT_2_Axis_Camera/in_situ_absorption": "camera_2",
}

### Set global path for experiment

In [4]:
img_dir = '//DyLabNAS/Data/'
SequenceName = "Evaporative_Cooling" + "/"
folderPath = img_dir + SequenceName + '2023/04/17'# get_date()

### Load shot 0058

In [5]:
shotNum = "0058"
filePath = folderPath + "/" + shotNum + "/*.h5"

dataSetDict = {
    dskey[groupList[i]]: read_hdf5_file(filePath, groupList[i])
    for i in [0] # range(len(groupList)) # uncommont to load data for all three cameras
}
dataSet = dataSetDict["camera_0"]

dataSet = swap_xy(dataSet)

scanAxis = get_scanAxis(dataSet)

dataSet = auto_rechunk(dataSet)

dataSet.load()

<xarray.Dataset>
Dimensions:           (runs: 5, truncation_value: 11, y: 1200, x: 1920)
Coordinates:
  * runs              (runs) float64 0.0 1.0 2.0 3.0 4.0
  * truncation_value  (truncation_value) float64 0.8 0.83 0.85 ... 0.97 0.99 1.0
Dimensions without coordinates: y, x
Data variables:
    atoms             (runs, truncation_value, y, x) uint16 99 100 ... 126 129
    background        (runs, truncation_value, y, x) uint16 103 100 ... 122 124
    dark              (runs, truncation_value, y, x) uint16 51 52 52 ... 49 50
    shotNum           (runs, truncation_value) <U2 '00' '01' '02' ... '53' '54'
Attributes: (12/100)
    TOF_free:                          0.02
    abs_img_freq:                      110.866
    absorption_imaging_flag:           True
    backup_data:                       True
    blink_off_time:                    nan
    blink_on_time:                     nan
    ...                                ...
    z_offset:                          0.195
    z_offset_img:                      0.195
    truncation_value:                  [0.8  0.83 0.85 0.87 0.89 0.91 0.93 0....
    runs:                              [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 1...
    scanAxis:                          ['runs' 'truncation_value']
    scanAxisLength:                    [55. 55.]

## Index and select data

Since we use the xarray package, in fact, it already has a well developed function to index and select the data. Therefore, have a look of the following link

https://docs.xarray.dev/en/stable/user-guide/indexing.html

## Modify the data

There are two ways to select an element in xarray and modify the value of it.

### Select by value

The first method is to select it by the value of coordiante.

Here is an emaxple of selecting the element in 'ShotNum' at 'runs'=0, truncation_value=0.8, and change it to '-1'.

In [6]:
dataSet.shotNum.loc[
        {
            'runs': 0,
            'truncation_value': 0.8,
        }
    ] = '-1'

# Or wirte it in short
dataSet.shotNum.loc[0, 0.8] = '-1'

dataSet.shotNum

<xarray.DataArray 'shotNum' (runs: 5, truncation_value: 11)>
array([['-1', '01', '02', '03', '04', '05', '06', '07', '08', '09', '10'],
       ['11', '12', '13', '14', '15', '16', '17', '18', '19', '20', '21'],
       ['22', '23', '24', '25', '26', '27', '28', '29', '30', '31', '32'],
       ['33', '34', '35', '36', '37', '38', '39', '40', '41', '42', '43'],
       ['44', '45', '46', '47', '48', '49', '50', '51', '52', '53', '54']],
      dtype='<U2')
Coordinates:
  * runs              (runs) float64 0.0 1.0 2.0 3.0 4.0
  * truncation_value  (truncation_value) float64 0.8 0.83 0.85 ... 0.97 0.99 1.0

### Select by index

The second method is to select it by index.

Here is an emaxple of selecting the element in 'ShotNum' at (0, 1), and change it to '-2'.

In [7]:
dataSet.shotNum[0, 1] = '-2'
dataSet.shotNum

<xarray.DataArray 'shotNum' (runs: 5, truncation_value: 11)>
array([['-1', '-2', '02', '03', '04', '05', '06', '07', '08', '09', '10'],
       ['11', '12', '13', '14', '15', '16', '17', '18', '19', '20', '21'],
       ['22', '23', '24', '25', '26', '27', '28', '29', '30', '31', '32'],
       ['33', '34', '35', '36', '37', '38', '39', '40', '41', '42', '43'],
       ['44', '45', '46', '47', '48', '49', '50', '51', '52', '53', '54']],
      dtype='<U2')
Coordinates:
  * runs              (runs) float64 0.0 1.0 2.0 3.0 4.0
  * truncation_value  (truncation_value) float64 0.8 0.83 0.85 ... 0.97 0.99 1.0

## Remove the data

### Simply remove element or variables

For simply remove elements or variables in xarray, please read the introduction and examples from xarray package in the following link

    https://docs.xarray.dev/en/stable/generated/xarray.Dataset.drop_vars.html
    https://docs.xarray.dev/en/latest/generated/xarray.Dataset.drop_sel.html
    https://docs.xarray.dev/en/latest/generated/xarray.Dataset.drop_isel.html

### Remove bad shot

However, if one wants to remove the bad shot, it is highly recommended to set the value to 'np.nan', instead of directly delete it.

In order to do that, except the two ways we demenstrate in the section 'Modify the data', we also implent a function to do it.

In [8]:
data = copy.deepcopy(dataSet.atoms)
# we first need to change the dtype from unsign 16-bit integer (uint16) to float, 
# since the uint16 doesn't support to store nan value.
data = data.astype(float)
data = remove_bad_shots(data, runs=0, truncation_value=0.8)
data

<xarray.DataArray 'atoms' (runs: 5, truncation_value: 11, y: 1200, x: 1920)>
array([[[[ nan,  nan,  nan, ...,  nan,  nan,  nan],
         [ nan,  nan,  nan, ...,  nan,  nan,  nan],
         [ nan,  nan,  nan, ...,  nan,  nan,  nan],
         ...,
         [ nan,  nan,  nan, ...,  nan,  nan,  nan],
         [ nan,  nan,  nan, ...,  nan,  nan,  nan],
         [ nan,  nan,  nan, ...,  nan,  nan,  nan]],

        [[102., 103., 100., ..., 155., 154., 142.],
         [ 97., 100., 101., ..., 146., 146., 156.],
         [ 91.,  93.,  97., ..., 142., 136., 151.],
         ...,
         [105., 103., 103., ..., 144., 134., 142.],
         [102., 104., 112., ..., 133., 134., 135.],
         [114., 115., 113., ..., 119., 126., 122.]],

        [[101., 105., 103., ..., 148., 152., 146.],
         [101., 102.,  98., ..., 143., 146., 149.],
         [ 97.,  98.,  98., ..., 139., 137., 146.],
         ...,
...
         ...,
         [100., 102., 109., ..., 135., 141., 140.],
         [106., 103., 105., ..., 128., 140., 132.],
         [114., 107., 108., ..., 121., 123., 126.]],

        [[101., 102., 101., ..., 153., 153., 146.],
         [101., 103., 100., ..., 148., 143., 149.],
         [ 96.,  95.,  98., ..., 145., 138., 144.],
         ...,
         [ 98., 107., 103., ..., 140., 142., 145.],
         [106., 100., 103., ..., 133., 133., 136.],
         [115., 103., 102., ..., 123., 125., 128.]],

        [[103., 100., 102., ..., 154., 147., 153.],
         [ 96., 103.,  97., ..., 150., 150., 152.],
         [ 96., 100.,  96., ..., 141., 142., 144.],
         ...,
         [101., 102., 101., ..., 139., 142., 140.],
         [105., 105.,  98., ..., 132., 135., 131.],
         [109., 111., 107., ..., 125., 126., 129.]]]])
Coordinates:
  * runs              (runs) float64 0.0 1.0 2.0 3.0 4.0
  * truncation_value  (truncation_value) float64 0.8 0.83 0.85 ... 0.97 0.99 1.0
Dimensions without coordinates: y, x
Attributes:
    IMAGE_SUBCLASS:       IMAGE_GRAYSCALE
    IMAGE_VERSION:        1.2
    IMAGE_WHITE_IS_ZERO:  0